In [1]:
import sys
sys.path.append('../src')
from lora_model import LORAEngineGeneration
from influence import IFEngineGeneration
import datasets
import numpy as np
from collections import Counter
from datasets import Dataset
import collections
from tqdm.auto import tqdm
import pandas as pd
import os
import json

In [3]:
from sentence_transformers import SentenceTransformer,util

cos_model = SentenceTransformer("all-mpnet-base-v2")

RuntimeError: CUDA error: out of memory
CUDA kernel errors might be asynchronously reported at some other API call, so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.


In [ ]:
train_dataset = Dataset.load_from_disk("/nas02/Hadi/Incontenxt-influence/DataInf/datasets/hellaswag-train-900.hf")
validation_dataset = Dataset.load_from_disk("/nas02/Hadi/Incontenxt-influence/DataInf/datasets/hellaswag-test-100.hf")

In [ ]:
type(train_dataset['text'])

list

In [ ]:
train_encoded=cos_model.encode(train_dataset['text'])

In [56]:
len(train_encoded)

900

In [57]:
test_encoded=cos_model.encode(validation_dataset['text'])

In [58]:
len(test_encoded)

100

In [59]:
indices_picked=set()
mapping_dict=collections.defaultdict(list)
train_encoded=cos_model.encode(train_dataset['text'])
test_encoded=cos_model.encode(validation_dataset['text'])
for k,test in tqdm(enumerate(test_encoded)):
    
    sim=util.cos_sim(test,train_encoded)
    vals=np.argsort(sim)
    mapping_dict[k]=vals[0][0:100]
    for val in vals[0][0:100]:
        indices_picked.add(val.item())

0it [00:00, ?it/s]

In [60]:
len(indices_picked)


486

In [52]:
indices_picked

{1,
 2,
 3,
 5,
 7,
 8,
 10,
 11,
 13,
 14,
 16,
 18,
 20,
 25,
 27,
 28,
 30,
 31,
 32,
 35,
 36,
 38,
 39,
 40,
 41,
 42,
 43,
 45,
 46,
 53,
 54,
 56,
 57,
 59,
 61,
 62,
 65,
 66,
 69,
 70,
 73,
 76,
 77,
 78,
 81,
 85,
 86,
 87,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 99,
 100,
 102,
 104,
 106,
 108,
 109,
 110,
 111,
 112,
 115,
 117,
 118,
 119,
 120,
 121,
 124,
 126,
 128,
 129,
 131,
 133,
 135,
 136,
 137,
 138,
 139,
 143,
 144,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 156,
 157,
 159,
 160,
 161,
 163,
 164,
 165,
 169,
 170,
 171,
 175,
 176,
 178,
 179,
 180,
 181,
 182,
 185,
 186,
 187,
 189,
 190,
 191,
 192,
 195,
 196,
 198,
 199,
 201,
 202,
 203,
 205,
 206,
 207,
 209,
 212,
 213,
 214,
 215,
 216,
 221,
 223,
 225,
 226,
 227,
 229,
 231,
 233,
 234,
 237,
 239,
 240,
 241,
 242,
 245,
 248,
 249,
 251,
 253,
 254,
 257,
 258,
 259,
 260,
 262,
 263,
 266,
 268,
 274,
 275,
 279,
 280,
 281,
 286,
 287,
 289,
 292,
 293,
 296,
 298,
 299,
 302,
 303,
 305,
 306,


In [37]:
len(mapping_dict[0])

100

In [38]:
mapping_dict[1]

tensor([ 87, 404, 161,  36, 522,  27, 146, 497, 815, 792, 551, 451, 369, 822,
        213, 128, 163, 306, 802, 274, 709, 303, 750, 698, 314, 115, 338, 479,
         85, 652, 554, 302, 434, 644, 516, 460, 268, 670, 790, 233,  43,  65,
        240, 411, 851, 523, 454, 535, 354, 806, 440, 405, 690, 242,  59, 546,
        843, 447, 169, 344, 119, 402, 624, 474, 550, 657,  35, 876, 374, 796,
        186, 738, 778, 880, 392, 864,  62, 368, 281, 787, 121,  70, 280, 449,
         93, 634, 165, 490, 159,   1, 623, 397, 890, 442, 443, 655, 763, 869,
        734, 420])

In [111]:
data=datasets.load_dataset('glue', 'qnli')

In [112]:
data

DatasetDict({
    train: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 104743
    })
    validation: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 5463
    })
    test: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 5463
    })
})

In [113]:
data_train=data['train']

In [114]:
data['validation'] = data['validation'].select([*range(0,100,1)])

In [115]:
data_test=data['validation']

In [118]:
data_train

Dataset({
    features: ['question', 'sentence', 'label', 'idx'],
    num_rows: 104743
})

In [119]:
data_test

Dataset({
    features: ['question', 'sentence', 'label', 'idx'],
    num_rows: 100
})

In [120]:
train_text=[]
for sentence, question,label in zip(data_train['sentence'],data_train['question'],data_train['label']):
    if label==1:
        target='Yes'
    else:
        target='No'
        
    train_text.append('<s>Answer the following questions given the passage as Yes or No:{} Can we know {}\n{}</s>'.format(sentence,question,target))
print('<s>[INST]Answer the following questions given the passage as Yes or No:[/INST] {} Can we know {} {}</s>'.format(sentence,question,target))

<s>[INST]Answer the following questions given the passage as Yes or No:[/INST] Public expenditure health was at 8.9% of the GDP in 2004, whereas private expenditure was at 1.3%. Can we know How much of the gross domestic product was spent on public health in 2004? No</s>


In [121]:
test_text=[]
for sentence, question,label in zip(data_test['sentence'],data_test['question'],data_test['label']):
    if label==0:
        target='Yes'
    else:
        target='No'
        
    test_text.append('<s>[INST]Answer the following questions given the passage as Yes or No:[/INST] {} Can we know {}\n{}</s>'.format(sentence,question,target))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? {}</s>'.format(sentence,question,target))

Answer the following questions given the passage as Yes or No: The steam engine contributed much to the development of thermodynamic theory; however, the only applications of scientific theory that influenced the steam engine were the original concepts of harnessing the power of steam and atmospheric pressure and knowledge of properties of heat and steam. Can we know What was developed from Watt's measurements on a model steam engine?? Yes</s>


In [122]:
train_encoded=model.encode(train_text)

In [123]:
train_encoded[6]

array([ 4.99825999e-02,  1.40567934e-02, -1.13873566e-02,  5.31597696e-02,
       -3.58245187e-02, -1.34710153e-03, -1.84337702e-02,  1.50262360e-02,
        2.97735501e-02, -1.32922316e-02,  9.80024226e-03,  3.14931720e-02,
        5.57362512e-02, -7.12007284e-02,  3.20598967e-02, -2.49274597e-02,
        3.15554366e-02, -6.56321459e-03,  4.17179894e-03, -1.85594391e-02,
        3.17597901e-03, -4.67608823e-03, -1.77063216e-02,  1.91501826e-02,
        3.32072042e-02,  2.73431204e-02, -3.54995094e-02, -3.82498167e-02,
        1.06859673e-02, -2.39637308e-02,  6.14251457e-02,  3.15222261e-03,
       -2.60068402e-02, -4.21417616e-02,  1.77400375e-06, -1.60370264e-02,
        3.04199159e-02,  3.53617854e-02, -5.13780564e-02,  1.50314635e-02,
        3.21009569e-03,  5.74957132e-02, -5.54447435e-03, -3.69342491e-02,
       -4.82794084e-02, -6.60094321e-02,  2.68679690e-02, -9.54557210e-03,
       -7.44284177e-03,  4.66612466e-02,  2.62293033e-03,  4.72069122e-02,
       -1.31986209e-03, -

In [124]:
test_encoded=model.encode(test_text)

In [125]:
len(test_encoded)

100

In [126]:
indices_already=set()
train_selected=[]
for test in test_encoded:
    top9_list=[]
    sim=util.cos_sim(test,train_encoded)
    vals=np.argsort(sim)
    #print(vals[0])
    i=0
    while len(top9_list)<90:  #change to 9
        if vals[0][i].item() in indices_already:
            i+=1
            continue
        else:
            top9_list.append(vals[0][i].item())
            indices_already.add(vals[0][i].item())
            i+=1
    train_selected.extend(top9_list)
        
   

In [127]:
len(train_selected)

9000

In [128]:
len(set(train_selected))

9000

In [129]:
data['train'] = data['train'].select(train_selected)

In [130]:
data

DatasetDict({
    train: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 9000
    })
    validation: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 100
    })
    test: Dataset({
        features: ['question', 'sentence', 'label', 'idx'],
        num_rows: 5463
    })
})

In [131]:
data_train=data['train']

In [132]:
data_test=data['validation']

In [133]:
train_text=[]
for sentence, question,label in zip(data_train['sentence'],data_train['question'],data_train['label']):
    if label==0:
        target='Yes'
    else:
        target='No'
        
    train_text.append('<s>### Human: Answer the following questions given the passage as Yes or No:{} Can we know {}\n### Assistant: {}</s>'.format(sentence,question,target))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? {}</s>'.format(sentence,question,target))

Answer the following questions given the passage as Yes or No: Beyoncé voiced Queen Tara in the 3D CGI animated film, Epic, released by 20th Century Fox on May 24, and recorded an original song for the film, "Rise Up", co-written with Sia. Can we know What song did Beyonce record for the film Epic?? No</s>


In [134]:
data_train=data_train.add_column('text',train_text)

Flattening the indices:   0%|          | 0/9000 [00:00<?, ? examples/s]

In [135]:
train_prompt=[]
for sentence, question,label in zip(data_train['sentence'],data_train['question'],data_train['label']):
    if label==0:
        target='Yes'
    else:
        target='No'
        
    train_prompt.append('<s>### Human: Answer the following questions given the passage as Yes or No:{} Can we know {}\n### Assistant: </s>'.format(sentence,question))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? {}</s>'.format(sentence,question,target))

Answer the following questions given the passage as Yes or No: Beyoncé voiced Queen Tara in the 3D CGI animated film, Epic, released by 20th Century Fox on May 24, and recorded an original song for the film, "Rise Up", co-written with Sia. Can we know What song did Beyonce record for the film Epic?? No</s>


In [136]:
data_train=data_train.add_column('prompt',train_prompt)

In [137]:
test_text=[]
for sentence, question,label in zip(data_test['sentence'],data_test['question'],data_test['label']):
    if label==0:
        target='Yes'
    else:
        target='No'
        
    test_text.append('<s>### Human: Answer the following questions given the passage as Yes or No: {} Can we know {} ### Assistant: </s>'.format(sentence,question))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? </s>'.format(sentence,question))

Answer the following questions given the passage as Yes or No: The steam engine contributed much to the development of thermodynamic theory; however, the only applications of scientific theory that influenced the steam engine were the original concepts of harnessing the power of steam and atmospheric pressure and knowledge of properties of heat and steam. Can we know What was developed from Watt's measurements on a model steam engine?? </s>


In [138]:
data_test=data_test.add_column('text',test_text)

In [139]:
data_test=data_test.add_column('prompt',test_text)

In [140]:
data_train.save_to_disk('../datasets/qnli-similar-train-9000.hf')

Saving the dataset (0/1 shards):   0%|          | 0/9000 [00:00<?, ? examples/s]

In [141]:
data_test.save_to_disk('../datasets/qnli-similar-test-100-no-label.hf')

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [5]:
data_test=datasets.load_from_disk('../datasets/qnli-similar-test-100-no-label.hf')

In [6]:
data_test

Dataset({
    features: ['question', 'sentence', 'label', 'idx', 'text'],
    num_rows: 100
})

In [7]:
data_test['text']

['<s>### Human: Answer the following questions given the passage as Yes or No: As of that day, the new constitution heralding the Second Republic came into force. Can we know What came into force after the new constitution was herald? ### Assistant: </s>',
 '<s>### Human: Answer the following questions given the passage as Yes or No: The most important tributaries in this area are the Ill below of Strasbourg, the Neckar in Mannheim and the Main across from Mainz. Can we know What is the first major city in the stream of the Rhine? ### Assistant: </s>',
 "<s>### Human: Answer the following questions given the passage as Yes or No: In most provinces a second Bachelor's Degree such as a Bachelor of Education is required to become a qualified teacher. Can we know What is the minimum required if you want to teach in Canada? ### Assistant: </s>",
 "<s>### Human: Answer the following questions given the passage as Yes or No: The Tayichi'ud enslaved Temüjin (reportedly with a cangue, a sort of

In [3]:
data=datasets.load_dataset('ag_news')

In [4]:
data['train'] = data['train'].select([*range(0,9000,1)])

In [5]:
data['test'] = data['test'].select([*range(0,100,1)])

In [6]:
data_train=data['train']

In [7]:
data_test=data['test']

In [60]:
data=datasets.load_dataset('gsm8k', 'main')

In [61]:
data['train'] = data['train'].select([*range(0,900,1)])
data['test'] = data['test'].select([*range(0,100,1)])

In [62]:
data_train=data['train']
data_test=data['test']

In [63]:
text=[]
for question, answer in zip(data_train['question'],data_train['answer']):
    text.append('<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: {}[/INST]\n### Solution: {}</s>'.format(question,answer))

In [64]:
len(text)

900

In [65]:
prompt=[]
for question in data_train['question']:
    prompt.append('<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: {}[/INST]\nSolution: </s>'.format(question))

In [66]:
data_train=data_train.add_column('text',text)
data_train=data_train.add_column('prompt',prompt)

In [67]:
text=[]
for question, answer in zip(data_test['question'],data_test['answer']):
    text.append('<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: {}[/INST]\n### Solution: </s>'.format(question))

In [68]:
data_train['text']

['<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Natalia sold clips to 48 of her friends in April, and then she sold half as many clips in May. How many clips did Natalia sell altogether in April and May?[/INST]\n### Solution: Natalia sold 48/2 = <<48/2=24>>24 clips in May.\nNatalia sold 48+24 = <<48+24=72>>72 clips altogether in April and May.\n#### 72</s>',
 '<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Weng earns $12 an hour for babysitting. Yesterday, she just did 50 minutes of babysitting. How much did she earn?[/INST]\n### Solution: Weng earns 12/60 = $<<12/60=0.2>>0.2 per minute.\nWorking 50 minutes, she earned 0.2 x 50 = $<<0.2*50=10>>10.\n#### 10</s>',
 "<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Betty is saving money for a new wallet which costs $100. Betty has only half of the money she needs. Her parents decided to gi

In [69]:
prompt=[]
for question in data_test['question']:
    prompt.append('<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: {}[/INST]\nSolution: </s>'.format(question))

In [70]:
data_test=data_test.add_column('text',text)
data_test=data_test.add_column('prompt',prompt)

In [71]:
data_test

Dataset({
    features: ['question', 'answer', 'text', 'prompt'],
    num_rows: 100
})

In [75]:
data_train['text']

['<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Natalia sold clips to 48 of her friends in April, and then she sold half as many clips in May. How many clips did Natalia sell altogether in April and May?[/INST]\n### Solution: Natalia sold 48/2 = <<48/2=24>>24 clips in May.\nNatalia sold 48+24 = <<48+24=72>>72 clips altogether in April and May.\n#### 72</s>',
 '<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Weng earns $12 an hour for babysitting. Yesterday, she just did 50 minutes of babysitting. How much did she earn?[/INST]\n### Solution: Weng earns 12/60 = $<<12/60=0.2>>0.2 per minute.\nWorking 50 minutes, she earned 0.2 x 50 = $<<0.2*50=10>>10.\n#### 10</s>',
 "<s>[INST]Answer the following question through careful, concise step-by-step reasoning. Question: Betty is saving money for a new wallet which costs $100. Betty has only half of the money she needs. Her parents decided to gi

In [76]:
data_train.save_to_disk('../datasets/gsm8k-train-900.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

In [77]:
data_test.save_to_disk('../datasets/gsm8k-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [31]:
data=datasets.load_dataset('glue', 'mnli')

In [32]:
data

DatasetDict({
    train: Dataset({
        features: ['premise', 'hypothesis', 'label', 'idx'],
        num_rows: 392702
    })
    validation_matched: Dataset({
        features: ['premise', 'hypothesis', 'label', 'idx'],
        num_rows: 9815
    })
    validation_mismatched: Dataset({
        features: ['premise', 'hypothesis', 'label', 'idx'],
        num_rows: 9832
    })
    test_matched: Dataset({
        features: ['premise', 'hypothesis', 'label', 'idx'],
        num_rows: 9796
    })
    test_mismatched: Dataset({
        features: ['premise', 'hypothesis', 'label', 'idx'],
        num_rows: 9847
    })
})

In [37]:
data['validation_matched']['label'][0:10]

[1, 2, 0, 2, 2, 2, 2, 1, 2, 1]

In [38]:
data['train'] = data['train'].select([*range(0,900,1)])
data['test'] = data['validation_matched'].select([*range(0,100,1)])

In [39]:
data_train=data['train']
data_train

Dataset({
    features: ['premise', 'hypothesis', 'label', 'idx'],
    num_rows: 900
})

In [40]:
data_train['label']

[1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 2,
 2,
 0,
 2,
 1,
 1,
 2,
 0,
 0,
 2,
 2,
 1,
 0,
 0,
 2,
 0,
 0,
 1,
 2,
 1,
 2,
 0,
 0,
 0,
 2,
 1,
 2,
 0,
 0,
 2,
 2,
 2,
 0,
 1,
 0,
 1,
 0,
 0,
 2,
 2,
 1,
 0,
 0,
 0,
 2,
 1,
 1,
 1,
 2,
 1,
 2,
 1,
 1,
 0,
 2,
 0,
 1,
 2,
 2,
 2,
 2,
 2,
 1,
 1,
 2,
 2,
 2,
 0,
 2,
 1,
 0,
 1,
 2,
 2,
 2,
 0,
 1,
 0,
 1,
 0,
 2,
 1,
 1,
 2,
 2,
 0,
 0,
 2,
 1,
 0,
 2,
 0,
 2,
 0,
 2,
 1,
 2,
 1,
 0,
 0,
 2,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 2,
 2,
 2,
 0,
 2,
 1,
 2,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 1,
 2,
 2,
 0,
 2,
 1,
 2,
 0,
 0,
 0,
 2,
 1,
 2,
 2,
 1,
 2,
 1,
 2,
 0,
 2,
 1,
 1,
 0,
 1,
 2,
 0,
 1,
 1,
 1,
 0,
 2,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 2,
 0,
 1,
 2,
 0,
 0,
 1,
 2,
 2,
 1,
 0,
 1,
 0,
 2,
 2,
 0,
 2,
 2,
 2,
 0,
 2,
 2,
 2,
 2,
 1,
 2,
 2,
 0,
 2,
 0,
 2,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 2,
 2,
 2,
 1,
 2,
 1,
 0,
 0,
 1,
 2,
 1,
 1,
 1,
 2,
 2,
 2,
 0,
 2,
 2,
 1,
 1,
 0,
 1,
 0,
 1,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 2,
 0,
 2,


In [41]:
data_test=data['test']
data_test

Dataset({
    features: ['premise', 'hypothesis', 'label', 'idx'],
    num_rows: 100
})

In [42]:
train_text=[]
for sentence, question,label in zip(data_train['premise'],data_train['hypothesis'],data_train['label']):
    if label==0:
        target='Yes'
    else:
        target='No'
        
    train_text.append('<s>[INST]### Human: Answer the following questions given the passage as Yes, Maybe or No: {} Can we know {}[\INST]\n### Assistant: {}</s>'.format(sentence,question,target))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? {}</s>'.format(sentence,question,target))

Answer the following questions given the passage as Yes or No: Dutch World, where all sorts of fictional characters created by Edmund Morris come out to play with children of all ages! Can we know Edmund Morris created a world called Dutch World, a place where made up characters can play with all children.? Yes</s>


In [43]:
data_train=data_train.add_column('text',train_text)

In [44]:
test_text=[]
for sentence, question,label in zip(data_test['premise'],data_test['hypothesis'],data_test['label']):
    if label==0:
        target='Yes'
    elif label==1:
        target='Maybe'
    else:
        target='No'
        
    test_text.append('<s>[INST]### Human: Answer the following questions given the passage as Yes, Maybe or No: {} Can we know {}[/INST]\n### Assistant: </s>'.format(sentence,question))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? </s>'.format(sentence,question))

Answer the following questions given the passage as Yes or No: Taking an ecumenical tack, nation officials in Chicago recently issued edicts commanding preachers to back off their anti-Semitic rhetoric. Can we know Nation officials in Chicago are involved in religious issues.? </s>


In [45]:
train_prompt=[]
for sentence, question,label in zip(data_train['premise'],data_train['hypothesis'],data_train['label']):
    if label==0:
        target='Yes'
    elif label==1:
        target='Maybe'
    else:
        target='No'
        
    train_prompt.append('<s>[INST]### Human: Answer the following questions given the passage as Yes, Maybe or No: {} Can we know {}[/INST]\n### Assistant: </s>'.format(sentence,question))
print('Answer the following questions given the passage as Yes or No: {} Can we know {}? {}</s>'.format(sentence,question,target))

Answer the following questions given the passage as Yes or No: Dutch World, where all sorts of fictional characters created by Edmund Morris come out to play with children of all ages! Can we know Edmund Morris created a world called Dutch World, a place where made up characters can play with all children.? Yes</s>


In [46]:
data_train=data_train.add_column('prompt',train_prompt)

In [47]:
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [48]:
data_train

Dataset({
    features: ['premise', 'hypothesis', 'label', 'idx', 'text', 'prompt'],
    num_rows: 900
})

In [49]:
data_train['label']

[1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 2,
 2,
 0,
 2,
 1,
 1,
 2,
 0,
 0,
 2,
 2,
 1,
 0,
 0,
 2,
 0,
 0,
 1,
 2,
 1,
 2,
 0,
 0,
 0,
 2,
 1,
 2,
 0,
 0,
 2,
 2,
 2,
 0,
 1,
 0,
 1,
 0,
 0,
 2,
 2,
 1,
 0,
 0,
 0,
 2,
 1,
 1,
 1,
 2,
 1,
 2,
 1,
 1,
 0,
 2,
 0,
 1,
 2,
 2,
 2,
 2,
 2,
 1,
 1,
 2,
 2,
 2,
 0,
 2,
 1,
 0,
 1,
 2,
 2,
 2,
 0,
 1,
 0,
 1,
 0,
 2,
 1,
 1,
 2,
 2,
 0,
 0,
 2,
 1,
 0,
 2,
 0,
 2,
 0,
 2,
 1,
 2,
 1,
 0,
 0,
 2,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 2,
 2,
 2,
 0,
 2,
 1,
 2,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 1,
 2,
 2,
 0,
 2,
 1,
 2,
 0,
 0,
 0,
 2,
 1,
 2,
 2,
 1,
 2,
 1,
 2,
 0,
 2,
 1,
 1,
 0,
 1,
 2,
 0,
 1,
 1,
 1,
 0,
 2,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 2,
 0,
 1,
 2,
 0,
 0,
 1,
 2,
 2,
 1,
 0,
 1,
 0,
 2,
 2,
 0,
 2,
 2,
 2,
 0,
 2,
 2,
 2,
 2,
 1,
 2,
 2,
 0,
 2,
 0,
 2,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 2,
 2,
 2,
 1,
 2,
 1,
 0,
 0,
 1,
 2,
 1,
 1,
 1,
 2,
 2,
 2,
 0,
 2,
 2,
 1,
 1,
 0,
 1,
 0,
 1,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 2,
 0,
 2,


In [50]:
data_test

Dataset({
    features: ['premise', 'hypothesis', 'label', 'idx', 'text', 'prompt'],
    num_rows: 100
})

In [51]:
data_test['label']

[1,
 2,
 0,
 2,
 2,
 2,
 2,
 1,
 2,
 1,
 2,
 2,
 2,
 0,
 1,
 0,
 0,
 0,
 1,
 2,
 1,
 0,
 1,
 1,
 1,
 2,
 1,
 2,
 1,
 1,
 0,
 0,
 2,
 0,
 0,
 1,
 1,
 0,
 0,
 2,
 1,
 2,
 0,
 2,
 2,
 2,
 0,
 0,
 0,
 0,
 1,
 2,
 0,
 1,
 2,
 1,
 0,
 2,
 2,
 1,
 1,
 0,
 1,
 2,
 2,
 1,
 0,
 2,
 0,
 0,
 2,
 0,
 2,
 2,
 2,
 1,
 0,
 1,
 2,
 2,
 0,
 0,
 1,
 2,
 1,
 2,
 0,
 1,
 0,
 0,
 1,
 1,
 2,
 0,
 0,
 1,
 0,
 0,
 1,
 0]

In [52]:
data_train.save_to_disk('../datasets/mnli-train-900.hf')
data_test.save_to_disk('../datasets/mnli-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [2]:
data=datasets.load_from_disk('../datasets/gsm8k-train-900.hf')

In [4]:
data

Dataset({
    features: ['question', 'answer', 'text', 'prompt'],
    num_rows: 900
})

In [6]:
data=datasets.load_dataset('glue', 'qqp')

In [7]:
data

DatasetDict({
    train: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 363846
    })
    validation: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 40430
    })
    test: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 390965
    })
})

In [8]:
data['train']['question1'][0]

'How is the life of a math student? Could you describe your own experiences?'

In [9]:
data['train']['question2'][0]

'Which level of prepration is enough for the exam jlpt5?'

In [10]:
data['train']['label'][0]

0

In [11]:
data['train'] = data['train'].select([*range(0,900,1)])
data['validation'] = data['validation'].select([*range(0,100,1)])

In [12]:
data

DatasetDict({
    train: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 900
    })
    validation: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 100
    })
    test: Dataset({
        features: ['question1', 'question2', 'label', 'idx'],
        num_rows: 390965
    })
})

In [13]:
data_train=data['train']
data_test=data['validation']

In [14]:
train_text=[]
for sentence, question,label in zip(data_train['question1'],data_train['question2'],data_train['label']):
    if label==0:
        target='No'
    else:
        target='Yes'
        
    train_text.append('<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: {} Sentence 2: {}[/INST]\n### Assistant: {}</s>'.format(sentence,question,target))


In [15]:
data_train=data_train.add_column('text',train_text)

In [16]:
train_prompt=[]
for sentence, question,label in zip(data_train['question1'],data_train['question2'],data_train['label']):
    if label==0:
        target='No'
    else:
        target='Yes'
        
    train_prompt.append('<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: {} Sentence 2: {}[/INST]\n### Assistant: </s>'.format(sentence,question))

In [17]:
data_train=data_train.add_column('prompt',train_prompt)

In [18]:
data_train['text']

['<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: How is the life of a math student? Could you describe your own experiences? Sentence 2: Which level of prepration is enough for the exam jlpt5?[/INST]\n### Assistant: No</s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: How do I control my horny emotions? Sentence 2: How do you control your horniness?[/INST]\n### Assistant: Yes</s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: What causes stool color to change to yellow? Sentence 2: What can cause stool to come out as little balls?[/INST]\n### Assistant: No</s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: What can one do after MBBS? Sentence 2: What do i do after my MBBS ?[/INST]\n### Assistant: Yes</s>',

In [19]:
test_text=[]
for sentence, question,label in zip(data_test['question1'],data_test['question2'],data_test['label']):
    if label==0:
        target='No'
    else:
        target='Yes'
        
    test_text.append('<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: {} Sentence 2: {}[/INST]\n### Assistant: </s>'.format(sentence,question))

In [20]:
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [21]:
data_test['text']

['<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: Why are African-Americans so beautiful? Sentence 2: Why are hispanics so beautiful?[/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: I want to pursue PhD in Computer Science about social network,what is the open problem in social networks? Sentence 2: I handle social media for a non-profit. Should I start going to social media networking events? Are there any good ones in the bay area?[/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: Is there a reason why we should travel alone? Sentence 2: What are some reasons to travel alone?[/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Are the following sentences semantically equivalent or not? Answer with Yes or No. Sentence 1: Why a

In [22]:
data_train.save_to_disk('../datasets/qqp-train-900.hf')
data_test.save_to_disk('../datasets/qqp-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [23]:
data=datasets.load_dataset('glue', 'sst2')

In [24]:
data

DatasetDict({
    train: Dataset({
        features: ['sentence', 'label', 'idx'],
        num_rows: 67349
    })
    validation: Dataset({
        features: ['sentence', 'label', 'idx'],
        num_rows: 872
    })
    test: Dataset({
        features: ['sentence', 'label', 'idx'],
        num_rows: 1821
    })
})

In [25]:
data['train'] = data['train'].select([*range(0,900,1)])
data['validation'] = data['validation'].select([*range(0,100,1)])

In [26]:
data_train=data['train']
data_test=data['validation']

In [27]:
train_text=[]
for sentence,label in zip(data_train['sentence'],data_train['label']):
    if label==0:
        target='Negative'
    else:
        target='Positive'
        
    train_text.append('<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: {} [/INST]\n### Assistant: {}</s>'.format(sentence,target))


In [28]:
data_train=data_train.add_column('text',train_text)

In [29]:
train_prompt=[]
for sentence,label in zip(data_train['sentence'],data_train['label']):
    if label==0:
        target='Negative'
    else:
        target='Positive'
        
    train_prompt.append('<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: {} [/INST]\n### Assistant: </s>'.format(sentence))


In [30]:
data_train=data_train.add_column('prompt',train_prompt)

In [31]:
data_train['prompt']

['<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: hide new secretions from the parental units  [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: contains no wit , only labored gags  [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: that loves its characters and communicates something rather beautiful about human nature  [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: remains utterly satisfied to remain the same throughout  [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: on the worst revenge-of-the-nerds clichés the filmmakers could dredge up  [/INST]\n### Assistant: </s>',
 "<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: that 's 

In [32]:
test_text=[]
for sentence,label in zip(data_test['sentence'],data_test['label']):
    if label==0:
        target='Negative'
    else:
        target='Positive'
        
    test_text.append('<s>[INST]### Human: Does the sentence have a negative or positive sentiment? Sentence: {} [/INST]\n### Assistant: </s>'.format(sentence))

In [33]:
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [34]:
data_train.save_to_disk('../datasets/sst-train-900.hf')
data_test.save_to_disk('../datasets/sst-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [59]:
data=datasets.load_dataset('hellaswag')

In [60]:
data

DatasetDict({
    train: Dataset({
        features: ['ind', 'activity_label', 'ctx_a', 'ctx_b', 'ctx', 'endings', 'source_id', 'split', 'split_type', 'label'],
        num_rows: 39905
    })
    test: Dataset({
        features: ['ind', 'activity_label', 'ctx_a', 'ctx_b', 'ctx', 'endings', 'source_id', 'split', 'split_type', 'label'],
        num_rows: 10003
    })
    validation: Dataset({
        features: ['ind', 'activity_label', 'ctx_a', 'ctx_b', 'ctx', 'endings', 'source_id', 'split', 'split_type', 'label'],
        num_rows: 10042
    })
})

In [61]:
data['train'] = data['train'].select([*range(0,900,1)])
data['validation'] = data['validation'].select([*range(0,100,1)])

In [62]:
data_train=data['train']
data_test=data['validation']

In [63]:
data_train

Dataset({
    features: ['ind', 'activity_label', 'ctx_a', 'ctx_b', 'ctx', 'endings', 'source_id', 'split', 'split_type', 'label'],
    num_rows: 900
})

In [64]:
data_train['endings']

[[', the man adds wax to the windshield and cuts it.',
  ', a person board a ski lift, while two men supporting the head of the person wearing winter clothes snow as the we girls sled.',
  ', the man puts on a christmas coat, knitted with netting.',
  ', the man continues removing the snow on his car.'],
 ['contain egg yolks and baking soda.',
  'are then sprinkled with brown sugar.',
  'are placed in a strainer on the counter.',
  'are filled with pastries and loaded into the oven.'],
 ['is seen moving on a board and cutting out its contents.',
  'hits the peeled cheesecake, followed by sliced custard and still cooked ice cream.',
  'etches a shape into the inside of the baked pans.',
  'is used to cut cylinder shaped dough into rounds.'],
 ['is placed onto a baked potato.',
  ', ls, and pickles are placed in the oven.',
  'is poured into a midden.',
  'is prepared then it is removed from the oven by a helper when done.'],
 ['is standing on the sponge cutting the hair of the person we

In [65]:
train_context=[]
for sentence, question,label in zip(data_train['ctx'],data_train['endings'],data_train['label']):
    
    train_context.append('Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: {}. Candidate Sentence 0: {} Candidate Sentence 1: {} Candidate Sentence 2: {} Candidate Sentence 3: {}'.format(sentence,question[0],question[1],question[2],question[3]))


In [66]:
train_text=[]
for sentence, question,label in zip(data_train['ctx'],data_train['endings'],data_train['label']):
    
    train_text.append('<s>[INST]### Human: Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: {}. Candidate Sentence 0: {} Candidate Sentence 1: {} Candidate Sentence 2: {} Candidate Sentence 3: {}[/INST]\n### Assistant: {}</s>'.format(sentence,question[0],question[1],question[2],question[3],label))


In [67]:
train_prompt=[]
for sentence, question in zip(data_train['ctx'],data_train['endings']):
    
    train_prompt.append('<s>[INST]### Human: Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: {}. Candidate Sentence 0: {} Candidate Sentence 1: {} Candidate Sentence 2: {} Candidate Sentence 3: {}[/INST]\n### Assistant: </s>'.format(sentence,question[0],question[1],question[2],question[3]))


In [68]:
data_train=data_train.add_column('context',train_context)

In [69]:
data_train=data_train.add_column('text',train_text)
data_train=data_train.add_column('prompt',train_prompt)


In [71]:
test_text=[]
for sentence, question in zip(data_test['ctx'],data_test['endings']):
    
    test_text.append('<s>[INST]### Human: Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: {}. Candidate Sentence 0: {} Candidate Sentence 1: {} Candidate Sentence 2: {} Candidate Sentence 3: {} [/INST]\n### Assistant: </s>'.format(sentence,question[0],question[1],question[2],question[3]))

In [73]:
test_context=[]
for sentence, question,label in zip(data_test['ctx'],data_test['endings'],data_test['label']):
    
    test_context.append('Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: {}. Candidate Sentence 0: {} Candidate Sentence 1: {} Candidate Sentence 2: {} Candidate Sentence 3: {}'.format(sentence,question[0],question[1],question[2],question[3]))

In [74]:
data_test=data_test.add_column('context',test_context)

In [75]:
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [78]:
data_train

Dataset({
    features: ['ind', 'activity_label', 'ctx_a', 'ctx_b', 'ctx', 'endings', 'source_id', 'split', 'split_type', 'label', 'context', 'text', 'prompt'],
    num_rows: 900
})

In [77]:
data_train.save_to_disk('../datasets/hellaswag-train-900.hf')
data_test.save_to_disk('../datasets/hellaswag-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [17]:
data_train_check=datasets.load_from_disk('../datasets/hellaswag-train-900.hf')
data_test_check=datasets.load_from_disk('../datasets/hellaswag-test-100.hf')

In [59]:
data_test_check['context']

["Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: A man is sitting on a roof. he. Candidate Sentence 0: is using wrap to wrap a pair of skis. Candidate Sentence 1: is ripping level tiles off. Candidate Sentence 2: is holding a rubik's cube. Candidate Sentence 3: starts pulling up roofing on a roof.",
 'Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: A lady walks to a barbell. She bends down and grabs the pole. the lady. Candidate Sentence 0: swings and lands in her arms. Candidate Sentence 1: pulls the barbell forward. Candidate Sentence 2: pulls a rope attached to the barbell. Candidate Sentence 3: stands and lifts the weight over her head.',
 'Which of the 4 candidate sentences best completes the initial sentence. Initial Sentence: Two women in a child are shown in a canoe while a man pulls the canoe while standing in the water, with other individuals visible in the background. the child and a differe

In [49]:
data_test

Dataset({
    features: ['sentence', 'label', 'idx', 'text', 'prompt'],
    num_rows: 100
})

In [41]:
data=datasets.load_dataset('tau/commonsense_qa')

In [42]:
data

DatasetDict({
    train: Dataset({
        features: ['id', 'question', 'question_concept', 'choices', 'answerKey'],
        num_rows: 9741
    })
    validation: Dataset({
        features: ['id', 'question', 'question_concept', 'choices', 'answerKey'],
        num_rows: 1221
    })
    test: Dataset({
        features: ['id', 'question', 'question_concept', 'choices', 'answerKey'],
        num_rows: 1140
    })
})

In [43]:
data['validation']

Dataset({
    features: ['id', 'question', 'question_concept', 'choices', 'answerKey'],
    num_rows: 1221
})

In [44]:
data['train'] = data['train'].select([*range(0,900,1)])
data['validation'] = data['validation'].select([*range(0,100,1)])

In [45]:
data_train=data['train']
data_test=data['validation']

Dataset({
    features: ['id', 'question', 'question_concept', 'choices', 'answerKey'],
    num_rows: 900
})

In [47]:
data_train['choices'][0]

{'label': ['A', 'B', 'C', 'D', 'E'],
 'text': ['ignore', 'enforce', 'authoritarian', 'yell at', 'avoid']}

In [48]:
train_context=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answerKey']):
    
    train_context.append('Which one of the 5 choices best answers the question. Question: {}. A: {}, B: {}, C: {}, D: {}, E: {}.'.format(sentence,question['text'][0],question['text'][1],question['text'][2],question['text'][3], question['text'][4]))

In [49]:
train_text=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answerKey']):
    
    train_text.append('<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: {}. A: {}, B: {}, C: {}, D: {}, E: {}. [/INST]\n### Assistant: {}</s>'.format(sentence,question['text'][0],question['text'][1],question['text'][2],question['text'][3], question['text'][4],label))


In [50]:
train_prompt=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answerKey']):
    
    train_prompt.append('<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: {}. A: {}, B: {}, C: {}, D: {}, E: {}. [/INST]\n### Assistant: </s>'.format(sentence,question['text'][0],question['text'][1],question['text'][2],question['text'][3], question['text'][4]))


In [51]:
train_text

['<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: The sanctions against the school were a punishing blow, and they seemed to what the efforts the school had made to change?. A: ignore, B: enforce, C: authoritarian, D: yell at, E: avoid. [/INST]\n### Assistant: A</s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Sammy wanted to go to where the people were.  Where might he go?. A: race track, B: populated areas, C: the desert, D: apartment, E: roadblock. [/INST]\n### Assistant: B</s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: To locate a choker not located in a jewelry box or boutique where would you go?. A: jewelry store, B: neck, C: jewlery box, D: jewelry box, E: boutique. [/INST]\n### Assistant: A</s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Google Maps and other highway and street GPS services have replaced what?. A

In [52]:
data_train=data_train.add_column('context',train_context)
data_train=data_train.add_column('text',train_text)
data_train=data_train.add_column('prompt',train_prompt)

In [55]:
data_train['prompt']

['<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: The sanctions against the school were a punishing blow, and they seemed to what the efforts the school had made to change?. A: ignore, B: enforce, C: authoritarian, D: yell at, E: avoid. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Sammy wanted to go to where the people were.  Where might he go?. A: race track, B: populated areas, C: the desert, D: apartment, E: roadblock. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: To locate a choker not located in a jewelry box or boutique where would you go?. A: jewelry store, B: neck, C: jewlery box, D: jewelry box, E: boutique. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Google Maps and other highway and street GPS services have replaced what?. A: u

In [64]:
test_text=[]
for sentence, question,label in zip(data_test['question'],data_test['choices'],data_test['answerKey']):
    
    test_text.append('<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: {}. A: {}, B: {}, C: {}, D: {}, E: {}. [/INST]\n### Assistant: </s>'.format(sentence,question['text'][0],question['text'][1],question['text'][2],question['text'][3], question['text'][4],label))


In [65]:
test_context=[]
for sentence, question,label in zip(data_test['question'],data_test['choices'],data_test['answerKey']):
    
    test_context.append('Which one of the 5 choices best answers the question. Question: {}. A: {}, B: {}, C: {}, D: {}, E: {}.'.format(sentence,question['text'][0],question['text'][1],question['text'][2],question['text'][3], question['text'][4]))

In [66]:
data_test=data_test.add_column('context',test_context)
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [69]:
data_test['prompt']

['<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: A revolving door is convenient for two direction travel, but it also serves as a security measure at a what?. A: bank, B: library, C: department store, D: mall, E: new york. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: What do people aim to do at work?. A: complete job, B: learn from each other, C: kill animals, D: wear hats, E: talk to each other. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Where would you find magazines along side many other printed works?. A: doctor, B: bookstore, C: market, D: train station, E: mortuary. [/INST]\n### Assistant: </s>',
 '<s>[INST]### Human: Which one of the 5 choices best answers the question. Question: Where are  you likely to find a hamburger?. A: fast food restaurant, B: pizza, C: ground up dead cows, D: mouth, E: cow c

In [70]:
data_train.save_to_disk('../datasets/cmsqa-train-900.hf')
data_test.save_to_disk('../datasets/cmsqa-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [2]:
data_train_check=datasets.load_from_disk('../datasets/cmsqa-train-900.hf')
data_test_check=datasets.load_from_disk('../datasets/cmsqa-test-100.hf')

In [14]:
data_test_check['context']

['Which one of the 4 choices best answers the question. Question: Comparisons of gay and lesbian couples with heterosexual married couples show that gay and lesbian couples. 0: Are far less satisfied with their relationship, 1: Show many of the same characteristics, 2: Always attempt to conceal their relationship, 3: Are usually more satisfied with their relationship.',
 'Which one of the 4 choices best answers the question. Question: One difference between the friendships of older and younger adults is that older adults. 0: Have far fewer friends, 1: Have more cross gender friendships, 2: Have more close friends, 3: Have less time for friends.',
 "Which one of the 4 choices best answers the question. Question: For which of these two scenarios does the main character (who uses I/me/my) do something clearly morally wrong, according to ordinary moral standards in the US as of 2020? Scenario 1 | I didn't think his wife was even remotely attractive, so I decided I would never ask her out e

In [32]:
data=datasets.load_dataset('cais/mmlu', 'all')

In [33]:
data

DatasetDict({
    test: Dataset({
        features: ['question', 'subject', 'choices', 'answer'],
        num_rows: 14042
    })
    validation: Dataset({
        features: ['question', 'subject', 'choices', 'answer'],
        num_rows: 1531
    })
    dev: Dataset({
        features: ['question', 'subject', 'choices', 'answer'],
        num_rows: 285
    })
    auxiliary_train: Dataset({
        features: ['question', 'subject', 'choices', 'answer'],
        num_rows: 99842
    })
})

In [34]:
data['validation']['answer']

[0,
 1,
 0,
 2,
 2,
 3,
 1,
 3,
 1,
 2,
 1,
 3,
 1,
 2,
 2,
 1,
 2,
 0,
 3,
 2,
 1,
 1,
 1,
 2,
 3,
 3,
 1,
 3,
 0,
 2,
 1,
 3,
 3,
 0,
 0,
 1,
 0,
 2,
 1,
 3,
 0,
 2,
 1,
 0,
 0,
 2,
 0,
 1,
 1,
 0,
 0,
 0,
 3,
 1,
 3,
 2,
 1,
 3,
 1,
 3,
 1,
 3,
 1,
 3,
 3,
 0,
 2,
 3,
 2,
 2,
 2,
 3,
 0,
 1,
 2,
 1,
 2,
 3,
 1,
 1,
 3,
 2,
 3,
 1,
 3,
 1,
 2,
 2,
 2,
 3,
 3,
 3,
 0,
 3,
 0,
 2,
 1,
 1,
 0,
 0,
 3,
 3,
 3,
 2,
 3,
 0,
 0,
 0,
 3,
 2,
 0,
 3,
 1,
 3,
 3,
 3,
 1,
 2,
 1,
 0,
 0,
 3,
 0,
 2,
 0,
 3,
 1,
 3,
 0,
 3,
 3,
 1,
 0,
 3,
 3,
 2,
 0,
 1,
 2,
 2,
 3,
 3,
 3,
 3,
 2,
 0,
 1,
 3,
 2,
 2,
 3,
 3,
 1,
 0,
 1,
 3,
 2,
 3,
 2,
 3,
 1,
 3,
 3,
 0,
 3,
 2,
 1,
 2,
 2,
 2,
 0,
 0,
 3,
 2,
 2,
 0,
 0,
 3,
 2,
 2,
 0,
 1,
 1,
 1,
 3,
 2,
 2,
 1,
 0,
 2,
 0,
 0,
 3,
 2,
 3,
 1,
 1,
 1,
 1,
 2,
 2,
 3,
 0,
 1,
 3,
 0,
 0,
 3,
 2,
 3,
 0,
 3,
 3,
 3,
 1,
 0,
 0,
 0,
 0,
 2,
 0,
 2,
 1,
 2,
 3,
 2,
 1,
 1,
 0,
 1,
 1,
 2,
 3,
 3,
 0,
 1,
 1,
 2,
 0,
 1,
 0,
 2,
 0,
 0,
 3,
 0,
 0,
 0,
 0,
 2,


In [35]:
subject_list=set(data['test']['subject'])

In [36]:
len(subject_list)

57

In [37]:
#Train Dataset

selected_indices=[]
for subject in subject_list:
    temp=[]
    for k,v in enumerate(data['test']['subject']):
        if v==subject:    # and k not in temp:
            temp.append(k)
        if len(temp)==16:
            break
    selected_indices.extend(temp)
        

In [38]:
selected_indices

[2569,
 2570,
 2571,
 2572,
 2573,
 2574,
 2575,
 2576,
 2577,
 2578,
 2579,
 2580,
 2581,
 2582,
 2583,
 2584,
 3645,
 3646,
 3647,
 3648,
 3649,
 3650,
 3651,
 3652,
 3653,
 3654,
 3655,
 3656,
 3657,
 3658,
 3659,
 3660,
 5432,
 5433,
 5434,
 5435,
 5436,
 5437,
 5438,
 5439,
 5440,
 5441,
 5442,
 5443,
 5444,
 5445,
 5446,
 5447,
 13049,
 13050,
 13051,
 13052,
 13053,
 13054,
 13055,
 13056,
 13057,
 13058,
 13059,
 13060,
 13061,
 13062,
 13063,
 13064,
 9714,
 9715,
 9716,
 9717,
 9718,
 9719,
 9720,
 9721,
 9722,
 9723,
 9724,
 9725,
 9726,
 9727,
 9728,
 9729,
 7284,
 7285,
 7286,
 7287,
 7288,
 7289,
 7290,
 7291,
 7292,
 7293,
 7294,
 7295,
 7296,
 7297,
 7298,
 7299,
 0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 9408,
 9409,
 9410,
 9411,
 9412,
 9413,
 9414,
 9415,
 9416,
 9417,
 9418,
 9419,
 9420,
 9421,
 9422,
 9423,
 3282,
 3283,
 3284,
 3285,
 3286,
 3287,
 3288,
 3289,
 3290,
 3291,
 3292,
 3293,
 3294,
 3295,
 3296,
 3297,
 10025,
 10026,
 1

In [39]:
data_train=data['test'].select(selected_indices)

In [40]:
data_train['subject']

['global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'global_facts',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_government_and_politics',
 'high_school_statistics',
 'high_school_statistics',
 'high_school_statistics',
 'high_

In [41]:
#Test Dataset
selected_indices=[]
for subject in subject_list:
    temp=[]
    for k,v in enumerate(data['validation']['subject']):
        if v==subject: # and k not in temp:
            temp.append(k)
        if len(temp)==2:
            break
    selected_indices.extend(temp)

In [42]:
len(selected_indices)


114

In [43]:
data_test=data['validation'].select(selected_indices)

In [44]:
data_test

Dataset({
    features: ['question', 'subject', 'choices', 'answer'],
    num_rows: 114
})

In [45]:
data_test['answer']

[1,
 2,
 0,
 3,
 3,
 3,
 0,
 2,
 3,
 1,
 1,
 0,
 0,
 1,
 0,
 2,
 1,
 2,
 2,
 3,
 1,
 3,
 1,
 1,
 1,
 0,
 1,
 0,
 2,
 0,
 3,
 1,
 0,
 3,
 1,
 0,
 3,
 1,
 1,
 2,
 1,
 1,
 1,
 1,
 0,
 0,
 2,
 0,
 3,
 0,
 1,
 1,
 3,
 1,
 0,
 3,
 0,
 0,
 3,
 3,
 1,
 0,
 3,
 3,
 0,
 2,
 2,
 2,
 1,
 0,
 1,
 2,
 3,
 0,
 0,
 1,
 2,
 3,
 3,
 1,
 2,
 2,
 3,
 1,
 2,
 3,
 0,
 1,
 3,
 3,
 1,
 0,
 0,
 1,
 2,
 0,
 3,
 2,
 1,
 0,
 3,
 3,
 0,
 2,
 1,
 0,
 2,
 1,
 1,
 1,
 2,
 0,
 2,
 1]

In [46]:
train_context=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answer']):
    
    train_context.append('Which one of the 4 choices best answers the question. Question: {}. 0: {}, 1: {}, 2: {}, 3: {}.'.format(sentence,question[0],question[1],question[2],question[3]))

In [47]:
train_context

['Which one of the 4 choices best answers the question. Question: As of 2016, about what percentage of adults aged 18 years or older were overweight?. 0: 10%, 1: 20%, 2: 40%, 3: 80%.',
 'Which one of the 4 choices best answers the question. Question: What was GDP per capita in the United States in 1850 when adjusting for inflation and PPP in 2011 prices?. 0: About $300, 1: About $3k, 2: About $8k, 3: About $15k.',
 'Which one of the 4 choices best answers the question. Question: As of 2019, about what percentage of people from the United States says homosexuality should be accepted by society?. 0: 52%, 1: 62%, 2: 72%, 3: 82%.',
 'Which one of the 4 choices best answers the question. Question: Which of the following countries generated the most total energy from solar sources in 2019?. 0: China, 1: United States, 2: Germany, 3: Japan.',
 'Which one of the 4 choices best answers the question. Question: Controlling for inflation and PPP-adjustment, about how much did GDP per capita increa

In [48]:
train_text=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answer']):
    
    train_text.append('<s>[INST]### Human: Which one of the 4 choices best answers the question. Question: {}. 0: {}, 1: {}, 2: {}, 3: {}. [/INST]\n### Assistant: {}</s>'.format(sentence,question[0],question[1],question[2],question[3],label))


In [49]:
train_prompt=[]
for sentence, question,label in zip(data_train['question'],data_train['choices'],data_train['answer']):
    
    train_prompt.append('<s>[INST]### Human: Which one of the 4 choices best answers the question. Question: {}. 0: {}, 1: {}, 2: {}, 3: {}. [/INST]\n### Assistant: </s>'.format(sentence,question[0],question[1],question[2],question[3]))


In [50]:
data_train=data_train.add_column('context',train_context)
data_train=data_train.add_column('text',train_text)
data_train=data_train.add_column('prompt',train_prompt)

In [51]:
test_context=[]
for sentence, question,label in zip(data_test['question'],data_test['choices'],data_test['answer']):
    
    test_context.append('Which one of the 4 choices best answers the question. Question: {}. 0: {}, 1: {}, 2: {}, 3: {}.'.format(sentence,question[0],question[1],question[2],question[3]))

In [52]:
test_text=[]
for sentence, question,label in zip(data_test['question'],data_test['choices'],data_test['answer']):
    
    test_text.append('<s>[INST]### Human: Which one of the 4 choices best answers the question. Question: {}. 0: {}, 1: {}, 2: {}, 3: {}. [/INST]\n### Assistant: </s>'.format(sentence,question[0],question[1],question[2],question[3]))


In [53]:
data_test=data_test.add_column('context',test_context)
data_test=data_test.add_column('text',test_text)
data_test=data_test.add_column('prompt',test_text)

In [54]:
data_train.save_to_disk('../datasets/mmlu-train-900.hf')
data_test.save_to_disk('../datasets/mmlu-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/912 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/114 [00:00<?, ? examples/s]

In [55]:
data_train_check=datasets.load_from_disk('../datasets/mmlu-train-900.hf')
data_test_check=datasets.load_from_disk('../datasets/mmlu-test-100.hf')

In [58]:
data_train_check

Dataset({
    features: ['question', 'subject', 'choices', 'answer', 'context', 'text', 'prompt'],
    num_rows: 912
})

In [57]:
data_train_check['context']

['Which one of the 4 choices best answers the question. Question: As of 2016, about what percentage of adults aged 18 years or older were overweight?. 0: 10%, 1: 20%, 2: 40%, 3: 80%.',
 'Which one of the 4 choices best answers the question. Question: What was GDP per capita in the United States in 1850 when adjusting for inflation and PPP in 2011 prices?. 0: About $300, 1: About $3k, 2: About $8k, 3: About $15k.',
 'Which one of the 4 choices best answers the question. Question: As of 2019, about what percentage of people from the United States says homosexuality should be accepted by society?. 0: 52%, 1: 62%, 2: 72%, 3: 82%.',
 'Which one of the 4 choices best answers the question. Question: Which of the following countries generated the most total energy from solar sources in 2019?. 0: China, 1: United States, 2: Germany, 3: Japan.',
 'Which one of the 4 choices best answers the question. Question: Controlling for inflation and PPP-adjustment, about how much did GDP per capita increa

In [93]:
data=datasets.load_dataset('mteb/banking77')

In [94]:
data

DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'label_text'],
        num_rows: 10003
    })
    test: Dataset({
        features: ['text', 'label', 'label_text'],
        num_rows: 3080
    })
})

In [95]:
classes=set(data['train']['label_text'])

In [96]:
classes

{'Refund_not_showing_up',
 'activate_my_card',
 'age_limit',
 'apple_pay_or_google_pay',
 'atm_support',
 'automatic_top_up',
 'balance_not_updated_after_bank_transfer',
 'balance_not_updated_after_cheque_or_cash_deposit',
 'beneficiary_not_allowed',
 'cancel_transfer',
 'card_about_to_expire',
 'card_acceptance',
 'card_arrival',
 'card_delivery_estimate',
 'card_linking',
 'card_not_working',
 'card_payment_fee_charged',
 'card_payment_not_recognised',
 'card_payment_wrong_exchange_rate',
 'card_swallowed',
 'cash_withdrawal_charge',
 'cash_withdrawal_not_recognised',
 'change_pin',
 'compromised_card',
 'contactless_not_working',
 'country_support',
 'declined_card_payment',
 'declined_cash_withdrawal',
 'declined_transfer',
 'direct_debit_payment_not_recognised',
 'disposable_card_limits',
 'edit_personal_details',
 'exchange_charge',
 'exchange_rate',
 'exchange_via_app',
 'extra_charge_on_statement',
 'failed_transfer',
 'fiat_currency_support',
 'get_disposable_virtual_card',
 '

In [97]:
#Train Dataset

selected_indices=[]
for subject in classes:
    temp=[]
    for k,v in enumerate(data['train']['label_text']):
        if v==subject and k not in temp:
            temp.append(k)
        if len(temp)==12:
            break
    selected_indices.extend(temp)
        

In [98]:
selected_indices


[9644,
 9645,
 9646,
 9647,
 9648,
 9649,
 9650,
 9651,
 9652,
 9653,
 9654,
 9655,
 2869,
 2870,
 2871,
 2872,
 2873,
 2874,
 2875,
 2876,
 2877,
 2878,
 2879,
 2880,
 737,
 738,
 739,
 740,
 741,
 742,
 743,
 744,
 745,
 746,
 747,
 748,
 6137,
 6138,
 6139,
 6140,
 6141,
 6142,
 6143,
 6144,
 6145,
 6146,
 6147,
 6148,
 7333,
 7334,
 7335,
 7336,
 7337,
 7338,
 7339,
 7340,
 7341,
 7342,
 7343,
 7344,
 1817,
 1818,
 1819,
 1820,
 1821,
 1822,
 1823,
 1824,
 1825,
 1826,
 1827,
 1828,
 1782,
 1783,
 1784,
 1785,
 1786,
 1787,
 1788,
 1789,
 1790,
 1791,
 1792,
 1793,
 0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 880,
 881,
 882,
 883,
 884,
 885,
 886,
 887,
 888,
 889,
 890,
 891,
 5092,
 5093,
 5094,
 5095,
 5096,
 5097,
 5098,
 5099,
 5100,
 5101,
 5102,
 5103,
 7005,
 7006,
 7007,
 7008,
 7009,
 7010,
 7011,
 7012,
 7013,
 7014,
 7015,
 7016,
 7161,
 7162,
 7163,
 7164,
 7165,
 7166,
 7167,
 7168,
 7169,
 7170,
 7171,
 7172,
 2698,
 2699,
 2700,
 2701,
 2702,
 2703,
 2704,
 

In [99]:
data_train=data['train'].select(selected_indices)

In [100]:
data_train=data_train.rename_column('text','text_old')

In [101]:
train_context=[]
for sentence,label in zip(data_train['text_old'],data_train['label_text']):
    
    train_context.append('What is the intent of the sentence. Sentence: {}.'.format(sentence))

In [102]:
train_text=[]
for sentence,label in zip(data_train['text_old'],data_train['label_text']):
    
    train_text.append('<s>[INST]### Human: What is the intent of the sentence. Sentence: {}. [/INST]\n### Assistant: {}</s>'.format(sentence,label))


In [103]:
train_prompt=[]
for sentence,label in zip(data_train['text_old'],data_train['label_text']):
    
    train_prompt.append('<s>[INST]### Human: What is the intent of the sentence. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [104]:
data_train=data_train.add_column('context',train_context)
data_train=data_train.add_column('text',train_text)
data_train=data_train.add_column('prompt',train_prompt)

In [105]:
data_train

Dataset({
    features: ['text_old', 'label', 'label_text', 'context', 'text', 'prompt'],
    num_rows: 924
})

In [106]:
#Test Dataset

selected_indices=[]
for subject in classes:
    temp=[]
    for k,v in enumerate(data['test']['label_text']):
        if v==subject and k not in temp:
            temp.append(k)
        if len(temp)==2:
            break
    selected_indices.extend(temp)

In [107]:
data_test=data['test'].select(selected_indices)

In [108]:
data_test=data_test.rename_column('text','text_old')

In [109]:
test_context=[]
for sentence,label in zip(data_test['text_old'],data_test['label_text']):
    
    test_context.append('What is the intent of the sentence. Sentence: {}.'.format(sentence))

In [110]:
test_prompt=[]
for sentence,label in zip(data_test['text_old'],data_test['label_text']):
    
    test_prompt.append('<s>[INST]### Human: What is the intent of the sentence. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [111]:
data_test=data_test.add_column('context',test_context)
data_test=data_test.add_column('text',test_prompt)
data_test=data_test.add_column('prompt',test_prompt)

In [112]:
data_test

Dataset({
    features: ['text_old', 'label', 'label_text', 'context', 'text', 'prompt'],
    num_rows: 154
})

In [113]:
data_train.save_to_disk('../datasets/banking77-train-900.hf')
data_test.save_to_disk('../datasets/banking77-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/924 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/154 [00:00<?, ? examples/s]

In [2]:
data_train_check=datasets.load_from_disk('../datasets/banking77-train-900.hf')
data_test_check=datasets.load_from_disk('../datasets/banking77-test-100.hf')

In [5]:
data_train_check['text']

['<s>[INST]### Human: What is the intent of the sentence. Sentence: Hi, I have an apple watch. How do I use it to top up my card?. [/INST]\n### Assistant: apple_pay_or_google_pay</s>',
 '<s>[INST]### Human: What is the intent of the sentence. Sentence: Can I use google pay to top up?. [/INST]\n### Assistant: apple_pay_or_google_pay</s>',
 '<s>[INST]### Human: What is the intent of the sentence. Sentence: why top up is not working even if I got my American Express in Apple Bay?. [/INST]\n### Assistant: apple_pay_or_google_pay</s>',
 '<s>[INST]### Human: What is the intent of the sentence. Sentence: Can I deposit money using Apple Pay?. [/INST]\n### Assistant: apple_pay_or_google_pay</s>',
 '<s>[INST]### Human: What is the intent of the sentence. Sentence: Can I use google pay for topping -up. [/INST]\n### Assistant: apple_pay_or_google_pay</s>',
 '<s>[INST]### Human: What is the intent of the sentence. Sentence: I do I top up from my Apple Watch?. [/INST]\n### Assistant: apple_pay_or_go

In [3]:
list(set(data_train_check['label_text']))

['receiving_money',
 'lost_or_stolen_phone',
 'transfer_timing',
 'get_physical_card',
 'get_disposable_virtual_card',
 'pin_blocked',
 'top_up_limits',
 'card_swallowed',
 'automatic_top_up',
 'card_about_to_expire',
 'failed_transfer',
 'top_up_by_cash_or_cheque',
 'unable_to_verify_identity',
 'pending_transfer',
 'card_payment_not_recognised',
 'declined_card_payment',
 'card_not_working',
 'change_pin',
 'verify_top_up',
 'lost_or_stolen_card',
 'direct_debit_payment_not_recognised',
 'fiat_currency_support',
 'wrong_amount_of_cash_received',
 'request_refund',
 'card_acceptance',
 'visa_or_mastercard',
 'Refund_not_showing_up',
 'getting_virtual_card',
 'why_verify_identity',
 'order_physical_card',
 'supported_cards_and_currencies',
 'top_up_by_bank_transfer_charge',
 'card_delivery_estimate',
 'edit_personal_details',
 'exchange_rate',
 'activate_my_card',
 'transfer_fee_charged',
 'contactless_not_working',
 'exchange_charge',
 'pending_card_payment',
 'balance_not_updated_aft

In [27]:
df_train=pd.read_csv('/nas03/Hadi/Incontext-influence/DataInf/datasets/cleaned_dataset_train.csv')
df_test=pd.read_csv('/nas03/Hadi/Incontext-influence/DataInf/datasets/cleaned_dataset_test.csv')

In [28]:
df_train.head()

tweet  sarcastic
0  the only thing i get from college be a caffein...          1
1  i love it when professor draw a big question m...          1
2  remember the hundred email from company when c...          1
3  today my pop pop tell me i be not force to go ...          1
4  i do too and i also report cancun cruz not wor...          1

In [29]:
df_sarcastic_sampled = df_train[df_train['sarcastic'] == 1].sample(n=450, random_state=42)

In [30]:
df_sarcastic_sampled

tweet  sarcastic
361  all the shade i have be hear about ben platt b...          1
422  you would think the odds of me sit next to the...          1
67   billy gunn sorta relevant for the first time i...          1
779  i see dettol toilet duck and zoflora be all tr...          1
394  arent you happy i give you less competition fo...          1
..                                                 ...        ...
590  my computer do this fun thing now where it sha...          1
144  but what be the rating reply to his tweet with...          1
617  just watch a man smoke crack on the r train in...          1
544  well do to the guy who be charge down the stai...          1
788                                             friend          1

[450 rows x 2 columns]

In [31]:
df_unsarcastic_sampled = df_train[df_train['sarcastic'] == 0].sample(n=450, random_state=42)

In [32]:
df_unsarcastic_sampled

tweet  sarcastic
2460  the new gossip girl be trash and im tire of pr...          0
1063  just try to make a hot chocolate use only cold...          0
1106                               steal from somewhere          0
2993  woman say they want a man who have his life to...          0
2454  my body be really out here sabotage me bc i ha...          0
...                                                 ...        ...
1182  if you drive dangerously on purpose youre the ...          0
1376     lord may my ego calm itself before i go insane          0
3118  do anyone else have to listen to extremely hig...          0
2899  his last delivery be 25 mile from my house he ...          0
2353  not generally if a community really annoy me i...          0

[450 rows x 2 columns]

In [33]:
new_df_train=pd.concat([df_sarcastic_sampled, df_unsarcastic_sampled])

In [34]:
new_df_train

tweet  sarcastic
361   all the shade i have be hear about ben platt b...          1
422   you would think the odds of me sit next to the...          1
67    billy gunn sorta relevant for the first time i...          1
779   i see dettol toilet duck and zoflora be all tr...          1
394   arent you happy i give you less competition fo...          1
...                                                 ...        ...
1182  if you drive dangerously on purpose youre the ...          0
1376     lord may my ego calm itself before i go insane          0
3118  do anyone else have to listen to extremely hig...          0
2899  his last delivery be 25 mile from my house he ...          0
2353  not generally if a community really annoy me i...          0

[900 rows x 2 columns]

In [35]:
data_array = new_df_train.values

In [36]:
np.random.seed(42)

In [37]:
np.random.shuffle(data_array)

In [38]:
shuffled_train = pd.DataFrame(data_array, columns=new_df_train.columns)

In [39]:
shuffled_train

tweet sarcastic
0    if anyone want to know how my night go i try m...         1
1    if drug be ban from sport why isnt makeup ban ...         0
2    only a a president a strong and decisive a wou...         1
3    how have marcel kittle be allow to use disc br...         0
4    what kind of sin have yall be commit for god t...         1
..                                                 ...       ...
895  im really look forward to not hug my friend an...         1
896     it would be nice if my body would let me sleep         1
897  i have such an obsession with white shoe but c...         0
898  ah yes people with eat disorder famous for eas...         1
899  i recover a repressed memory today of work at ...         1

[900 rows x 2 columns]

In [40]:
df_sarcastic_sampled_test = df_test[df_test['sarcastic'] == 1].sample(n=50, random_state=42)

In [41]:
df_unsarcastic_sampled_test = df_test[df_test['sarcastic'] == 0].sample(n=50, random_state=42)

In [42]:
new_df_test=pd.concat([df_sarcastic_sampled_test, df_unsarcastic_sampled_test])

In [43]:
new_df_test

tweet  sarcastic
731   i really love finish my term with an period of...          1
126   there be a bazillion thing to do in my small t...          1
246   yes i would absolutely love to see how my favo...          1
1160  oh great we have to wear mask and constant tes...          1
948              omicron case be go up run for the hill          1
...                                                 ...        ...
396              let keep build the africa that we want          0
412          get a jab couldnt be easy go and do it now          0
26    not on your life can you have democracy for th...          0
49            that away end be almost as bad a rashford          0
278   after 20 year in germany i have forget how dow...          0

[100 rows x 2 columns]

In [44]:
data_array = new_df_test.values

In [45]:
np.random.seed(42)

In [46]:
np.random.shuffle(data_array)

In [47]:
shuffled_test = pd.DataFrame(data_array, columns=new_df_test.columns)

In [48]:
ds_train=Dataset.from_pandas(shuffled_train)

In [49]:
ds_train

Dataset({
    features: ['tweet', 'sarcastic'],
    num_rows: 900
})

In [50]:
ds_train=ds_train.rename_column('tweet', 'original_text')

In [51]:
ds_train=ds_train.rename_column('sarcastic', 'label')

In [52]:
ds_test=Dataset.from_pandas(shuffled_test)

In [53]:
ds_test=ds_test.rename_column('tweet', 'original_text')

In [54]:
ds_test=ds_test.rename_column('sarcastic', 'label')

In [55]:
train_context=[]
for sentence,label in zip(ds_train['original_text'],ds_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    train_context.append('Is this sentence sarcastic or not. Sentence: {}.'.format(sentence))

In [56]:
train_context

['Is this sentence sarcastic or not. Sentence: if anyone want to know how my night go i try make a private story on snapchat and instead make a group chat i hate my life.',
 'Is this sentence sarcastic or not. Sentence: if drug be ban from sport why isnt makeup ban from beauty pageant.',
 'Is this sentence sarcastic or not. Sentence: only a a president a strong and decisive a would force the fda to ok a drug even before clinical trial result be in no need to wait for such silly formality people have be take the drug for year and most be still alive and fine #oktotry #gotrump.',
 'Is this sentence sarcastic or not. Sentence: how have marcel kittle be allow to use disc brake his year.',
 'Is this sentence sarcastic or not. Sentence: what kind of sin have yall be commit for god to punish u with this kinda weather.',
 'Is this sentence sarcastic or not. Sentence: come on tom ford #snooker #welshopen.',
 'Is this sentence sarcastic or not. Sentence: you guy how cool would a british version 

In [57]:
train_text=[]
for sentence,label in zip(ds_train['original_text'],ds_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    train_text.append('<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: {}. [/INST]\n### Assistant: {}</s>'.format(sentence,label))


In [58]:
train_text

['<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: if anyone want to know how my night go i try make a private story on snapchat and instead make a group chat i hate my life. [/INST]\n### Assistant: Yes</s>',
 '<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: if drug be ban from sport why isnt makeup ban from beauty pageant. [/INST]\n### Assistant: No</s>',
 '<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: only a a president a strong and decisive a would force the fda to ok a drug even before clinical trial result be in no need to wait for such silly formality people have be take the drug for year and most be still alive and fine #oktotry #gotrump. [/INST]\n### Assistant: Yes</s>',
 '<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: how have marcel kittle be allow to use disc brake his year. [/INST]\n### Assistant: No</s>',
 '<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: what kind of sin have yall be com

In [59]:
train_prompt=[]
for sentence,label in zip(ds_train['original_text'],ds_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    train_prompt.append('<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [60]:
ds_train=ds_train.add_column('context',train_context)
ds_train=ds_train.add_column('text',train_text)
ds_train=ds_train.add_column('prompt',train_prompt)

In [61]:
ds_train

Dataset({
    features: ['original_text', 'label', 'context', 'text', 'prompt'],
    num_rows: 900
})

In [62]:
test_context=[]
for sentence,label in zip(ds_test['original_text'],ds_test['label']):
    
    test_context.append('Is this sentence sarcastic or not. Sentence: {}.'.format(sentence))

In [63]:
test_prompt=[]
for sentence,label in zip(ds_test['original_text'],ds_test['label']):
    
    test_prompt.append('<s>[INST]### Human: Is this sentence sarcastic or not. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [64]:
ds_test=ds_test.add_column('context',test_context)
ds_test=ds_test.add_column('text',test_prompt)
ds_test=ds_test.add_column('prompt',test_prompt)

In [65]:
ds_train.save_to_disk('../datasets/isarcasm-train-900.hf')
ds_test.save_to_disk('../datasets/isarcasm-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [81]:
data_train_check=datasets.load_from_disk('../datasets/isarcasm-train-900.hf')
data_test_check=datasets.load_from_disk('../datasets/isarcasm-test-100.hf')

In [82]:
data_train_check

Dataset({
    features: ['original_text', 'label', 'context', 'text', 'prompt', 'label_text'],
    num_rows: 900
})

In [86]:
data_train_check['context']

['Is this sentence sarcastic or not. Sentence: if anyone want to know how my night go i try make a private story on snapchat and instead make a group chat i hate my life.',
 'Is this sentence sarcastic or not. Sentence: if drug be ban from sport why isnt makeup ban from beauty pageant.',
 'Is this sentence sarcastic or not. Sentence: only a a president a strong and decisive a would force the fda to ok a drug even before clinical trial result be in no need to wait for such silly formality people have be take the drug for year and most be still alive and fine #oktotry #gotrump.',
 'Is this sentence sarcastic or not. Sentence: how have marcel kittle be allow to use disc brake his year.',
 'Is this sentence sarcastic or not. Sentence: what kind of sin have yall be commit for god to punish u with this kinda weather.',
 'Is this sentence sarcastic or not. Sentence: come on tom ford #snooker #welshopen.',
 'Is this sentence sarcastic or not. Sentence: you guy how cool would a british version 

In [69]:
data_test_check

Dataset({
    features: ['original_text', 'label', 'context', 'text', 'prompt'],
    num_rows: 100
})

In [70]:
data_test_check['label_text']

KeyError: "Column label_text not in the dataset. Current columns in the dataset: ['original_text', 'label', 'context', 'text', 'prompt']"

In [73]:
label_text=[]
for label in (ds_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    label_text.append(label)

In [74]:
ds_train=ds_train.add_column('label_text',label_text)

In [75]:
label_text=[]
for label in (ds_test['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    label_text.append(label)

In [76]:
ds_test=ds_test.add_column('label_text',label_text)

In [79]:
ds_train.save_to_disk('../datasets/isarcasm-train-900.hf')
ds_test.save_to_disk('../datasets/isarcasm-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/900 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [88]:
data=datasets.load_dataset('glue', 'qnli')

data_train=datasets.load_from_disk('/nas02/Hadi/Incontenxt-influence/DataInf/datasets/isarcasm-train-900.hf')
data_test=datasets.load_from_disk('/nas02/Hadi/Incontenxt-influence/DataInf/datasets/isarcasm-test-100.hf')

data['train'] = data_train
data['validation'] = data_test

In [91]:
data['train']['label_text']

['Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 '

In [4]:
data=datasets.load_dataset('tweet_eval')

ValueError: Config name is missing.
Please pick one among the available configs: ['emoji', 'emotion', 'hate', 'irony', 'offensive', 'sentiment', 'stance_abortion', 'stance_atheism', 'stance_climate', 'stance_feminist', 'stance_hillary']
Example of usage:
	`load_dataset('tweet_eval', 'emoji')`

In [49]:
data=datasets.load_dataset('tweet_eval', 'irony')

In [50]:
data['test']

Dataset({
    features: ['text', 'label'],
    num_rows: 784
})

In [51]:
data['train'] = data['train'].select([*range(0,900,1)])
data['validation'] = data['validation'].select([*range(0,100,1)])

In [52]:
data_train=data['train']
data_test=data['validation']

In [53]:
data_train=data_train.rename_column('text','original_text')
data_test=data_test.rename_column('text','original_text')

In [54]:
data_train

Dataset({
    features: ['original_text', 'label'],
    num_rows: 900
})

In [55]:
train_context=[]
label_text=[]
for sentence,label in zip(data_train['original_text'],data_train['label']):
    if label==0:
        label="No"
        label_text.append(label)
    else:
        label="Yes"
        label_text.append(label)
    train_context.append('Is this sentence ironic or not. Sentence: {}.'.format(sentence))

In [56]:
train_text=[]
for sentence,label in zip(data_train['original_text'],data_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    train_text.append('<s>[INST]### Human: Is this sentence ironic or not. Sentence: {}. [/INST]\n### Assistant: {}</s>'.format(sentence,label))


In [57]:
train_prompt=[]
for sentence,label in zip(data_train['original_text'],data_train['label']):
    if label==0:
        label="No"
    else:
        label="Yes"
    train_prompt.append('<s>[INST]### Human: Is this sentence ironic or not. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [58]:
data_train=data_train.add_column('context',train_context)
data_train=data_train.add_column('text',train_text)
data_train=data_train.add_column('prompt',train_prompt)
data_train=data_train.add_column('label_text',label_text)

In [59]:
test_context=[]
for sentence,label in zip(data_test['original_text'],data_test['label']):
    
    test_context.append('Is this sentence ironic or not. Sentence: {}.'.format(sentence))

In [60]:
test_prompt=[]
test_label_text=[]
for sentence,label in zip(data_test['original_text'],data_test['label']):
    if label==0:
        label="No"
        test_label_text.append(label)
    else:
        label="Yes"
        test_label_text.append(label)
    
    test_prompt.append('<s>[INST]### Human: Is this sentence ironic or not. Sentence: {}. [/INST]\n### Assistant: </s>'.format(sentence))


In [61]:
data_test=data_test.add_column('context',test_context)
data_test=data_test.add_column('text',test_prompt)
data_test=data_test.add_column('prompt',test_prompt)
data_test=data_test.add_column('label_text',test_label_text)

In [46]:
data_train.save_to_disk('../datasets/tweetevalirony-train-900.hf')
data_test.save_to_disk('../datasets/tweetevalirony-test-100.hf')

PermissionError: Tried to overwrite /nas02/Hadi/Incontenxt-influence/DataInf/datasets/tweetevalirony-train-900.hf but a dataset can't overwrite itself.

In [2]:
data_train=datasets.load_from_disk('/nas02/Hadi/Incontenxt-influence/DataInf/datasets/tweetevalirony-train-900.hf')
data_test=datasets.load_from_disk('/nas02/Hadi/Incontenxt-influence/DataInf/datasets/tweetevalirony-test-100.hf')

In [3]:
data_train

Dataset({
    features: ['original_text', 'label', 'context', 'text', 'prompt', 'label_text'],
    num_rows: 900
})

In [4]:
data_test['label_text']

['Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'No',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'Yes',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'Yes',
 'No',
 'Yes',
 'Yes',
 'No',
 'Yes',
 'No',
 'No',
 'No',
 'No',
 'No']

In [5]:
data=[]
with open('/nas02/Hadi/Incontenxt-influence/DataInf/Indirect-ICL/sampled_data_30_binary/MMLU_abstract_algebra.json', 'r') as file:
    for line in file:
        json_data = json.loads(line)
        data.append(json_data)

In [6]:
text=[]
target=[]

for i in range(len(data)):
    text.append(data[i]['input'])
    target.append(data[i]['target'])

In [7]:
data_test

Dataset({
    features: ['original_text', 'label', 'context', 'text', 'prompt', 'label_text'],
    num_rows: 100
})

In [8]:
data_test=data_test.remove_columns(['context', 'text', 'prompt', 'label_text'])

In [9]:
#data_test['original_text']=text
data_test = data_test.remove_columns(['original_text']).add_column('original_text', text)

In [10]:
data_test=data_test.rename_column('original_text','text')

In [11]:
data_test = data_test.remove_columns(['label']).add_column('label', target)

In [12]:
data_test

Dataset({
    features: ['text', 'label'],
    num_rows: 100
})

In [13]:
data_test['text'][0:10]

['Q: Find the generator for the finite field Z_11.\nOptions:\n(B)2\n(C)3',
 'Q: Statement 1 | There exists a free abelian group of every positive integer rank. Statement 2 | A finitely generated abelian group is free abelian if its Betti number equals the number of elements in some generating set.\nOptions:\n(A)True, True\n',
 'Q: The inverse of -i in the multiplicative group, {1, -1, i , -i} is\nOptions:\n(C)i\n(D)-i',
 'Q: Statement 1 | Every group of order 42 has a normal subgroup of order 7. Statement 2 | Every group of order 42 has a normal subgroup of order 8.\nOptions:\n(A)True, True\n(C)True, False',
 'Q: Statement 1 | If a group has an element of order 10, then it has elements of orders 1, 2, and 5. Statement 2 | If a group has an element of order 2 and an element of order 3, then it has an element of order 6.\nOptions:\n(B)False, False\n(C)True, False',
 'Q: Compute the product in the given ring. (2,3)(3,5) in Z_5 x Z_9\nOptions:\n(B)(3,1)\n(C)(1,6)',
 'Q: Statement 1 | If a 

In [15]:
data_test['label'][0:10]

['(B)', '(A)', '(C)', '(C)', '(C)', '(C)', '(D)', '(C)', '(A)', '(C)']

In [20]:
data_test.save_to_disk('../Indirect-ICL/datasets/MMLU-algebra-test-100.hf')

Saving the dataset (0/1 shards):   0%|          | 0/100 [00:00<?, ? examples/s]

In [1]:
import json

In [42]:
data=[]
with open('/nas02/Hadi/Incontenxt-influence/DataInf/Indirect-ICL/cot_pool.json', 'r') as file:
    for line in file:
        json_data = json.loads(line)
        data.append(json_data)

In [43]:
data[1]

{'idx': 1,
 'cot': "Q: The short-run Phillips curve indicates a\n\nOptions:\n(A) direct relation between unemployment and inflation \n(D) inverse relation between unemployment and inflation\n\nA: Let's think step by step. We refer to Wikipedia articles on macroeconomics for help. The short-run Phillips curve shows that whenever unemployment decreases below a natural level, the inflation starts increasing, and vice-versa. \n\nSo the answer is (D).",
 'source': 'MMLU_high_school_macroeconomics',
 'pos': 1}

In [44]:
data[0]['cot'].split('\n')

['Q: Which of the following policies best describes supply-side fiscal policy?',
 '',
 'Options:',
 '(A) An increase in the money supply ',
 '(C) Lower taxes on research and development of new technology ',
 '',
 "A: Let's think step by step. We refer to Wikipedia articles on macroeconomics for help. Supply-side fiscal policy stimulates the economy by encouraging more production of goods and services through reduction in taxes and deregulation. ",
 '',
 'So the answer is (C).']

In [45]:
import re

In [63]:
text=[]
label=[]

# for i in range(len(data)):
#         try:
#             text.append(data[i]['cot'].split('\n\n')[0] +" "+ data[i]['cot'].split('\n\n')[1])
#             label.append(data[i]['cot'].split('\n\n')[-1].split()[-1].replace('.',''))
#         except:
#             print(data[i]['cot'].split('\n'))
#             text.append(data[i]['cot'].split('\n')[0] + " " + data[i]['cot'].split('\n')[1])
#             label.append(data[i]['cot'].split('\n')[-1].split()[-1].replace('.',''))


text=[]
label=[]    
for i in range(len(data)):
    temp=[]
    try:
        pattern = r"^\([A-Z]\)\s+\w"
        splits=data[i]['cot'].split('\n')
        splits_new=[x for x in splits if x]
        # splits_new_new=[x for x in splits_new if not x.startswith('A:')]
        # print(splits_new_new)
        for item in splits_new:
            if item.startswith("Q:"):
                temp.append(item)
        temp.append("Options:")
        results = [bool(re.match(pattern, sentence)) for sentence in splits_new]
        # print(results)
        for k, v in enumerate(results):
            if v == True:
                temp.append(splits_new[k])
                pass
        
        label.append(splits_new[-1].split()[-1].replace(".", ""))
    except Exception as e:
        print(e)
    text.append(" ".join(temp))

In [64]:
text

['Q: Which of the following policies best describes supply-side fiscal policy? Options: (A) An increase in the money supply  (C) Lower taxes on research and development of new technology ',
 'Q: The short-run Phillips curve indicates a Options: (A) direct relation between unemployment and inflation  (D) inverse relation between unemployment and inflation',
 'Q: Holding all else equal which of the following monetary policies would be used to boost U.S. exports? Options: (B) Increasing the reserve ratio  (C) Buying government securities ',
 'Q: Is the following sentence plausible? "Bam Adebayo scored a reverse layup in the Western Conference Finals." Options: (A) Yes (B) No',
 'Q: Is the following sentence plausible? "Santi Cazorla scored a touchdown." Options: (A) Yes (B) No',
 'Q: Is the following sentence plausible? "DeMar DeRozan was called for the goal tend." Options: (A) Yes (B) No',
 'Q: Glycolysis is the name given to the pathway involving the conversion of: Options: (A) glycogen

In [65]:
label

['(C)',
 '(D)',
 '(C)',
 '(A)',
 '(B)',
 '(A)',
 '(C)',
 '(B)',
 '(C)',
 '(B)',
 '(C)',
 '(D)',
 '(A)',
 '(A)',
 '(D)',
 '(A)',
 '(D)',
 '(D)',
 '(A)',
 '(A)',
 '(B)',
 '(B)',
 '(C)',
 '(D)',
 '(C)',
 '(C)',
 '(D)',
 '(B)',
 '(A)',
 '(C)',
 '(D)',
 '(A)',
 '(A)',
 '(D)',
 '(D)',
 '(A)',
 '(C)',
 '(D)',
 '(B)',
 '(A)',
 '(C)',
 '(C)',
 '(A)',
 '(D)',
 '(B)',
 '(A)',
 '(D)',
 '(A)',
 '(A)',
 '(A)',
 '(B)',
 '(D)',
 '(B)',
 '(B)',
 '(B)',
 '(A)',
 '(B)',
 '(C)',
 '(A)',
 '(A)',
 '(A)',
 '(C)',
 '(C)',
 '(B)',
 '(A)',
 '(C)',
 '(D)',
 '(C)',
 '(A)',
 '(B)',
 '(A)',
 '(C)',
 '(D)',
 '(B)',
 '(C)',
 '(A)',
 '(C)',
 '(B)',
 '(D)',
 '(D)',
 '(B)',
 '(B)',
 '(A)',
 '(B)']

In [66]:
len(text)

84

In [67]:
# data_test = data_test.remove_columns(['label'])

NameError: name 'data_test' is not defined

In [68]:
data_dict={"text":text, 'label':label}


In [71]:
from datasets import Dataset

In [72]:
data_train=Dataset.from_dict(data_dict)

In [73]:
data_train

Dataset({
    features: ['text', 'label'],
    num_rows: 84
})

In [74]:
data_train.save_to_disk('../Indirect-ICL/datasets/COT-train-84-new.hf')

Saving the dataset (0/1 shards):   0%|          | 0/84 [00:00<?, ? examples/s]

In [26]:
data_train=datasets.load_from_disk('../Indirect-ICL/datasets/MMLU-algebra-train-81-new.hf')
data_test=datasets.load_from_disk('../Indirect-ICL/datasets/MMLU-algebra-test-100.hf')

In [27]:
data_train

Dataset({
    features: ['text', 'label'],
    num_rows: 84
})

In [28]:
data_test

Dataset({
    features: ['text', 'label'],
    num_rows: 100
})

In [6]:
data_test=data_test.rename_column('original_text','text')

In [8]:
data_test.save_to_disk('../Indirect-ICL/datasets/MMLU-algebra-test-100.hf')

PermissionError: Tried to overwrite /nas02/Hadi/Incontenxt-influence/DataInf/Indirect-ICL/datasets/MMLU-algebra-test-100.hf but a dataset can't overwrite itself.

In [22]:
data_test['label']

['(B)',
 '(A)',
 '(C)',
 '(C)',
 '(C)',
 '(C)',
 '(D)',
 '(C)',
 '(A)',
 '(C)',
 '(D)',
 '(D)',
 '(C)',
 '(C)',
 '(A)',
 '(D)',
 '(C)',
 '(D)',
 '(A)',
 '(C)',
 '(B)',
 '(C)',
 '(A)',
 '(B)',
 '(D)',
 '(B)',
 '(D)',
 '(B)',
 '(A)',
 '(A)',
 '(D)',
 '(C)',
 '(D)',
 '(B)',
 '(A)',
 '(B)',
 '(C)',
 '(C)',
 '(C)',
 '(C)',
 '(C)',
 '(A)',
 '(A)',
 '(A)',
 '(A)',
 '(D)',
 '(C)',
 '(C)',
 '(C)',
 '(B)',
 '(D)',
 '(C)',
 '(D)',
 '(D)',
 '(A)',
 '(C)',
 '(B)',
 '(C)',
 '(A)',
 '(B)',
 '(A)',
 '(B)',
 '(D)',
 '(B)',
 '(B)',
 '(C)',
 '(B)',
 '(C)',
 '(A)',
 '(D)',
 '(B)',
 '(B)',
 '(B)',
 '(B)',
 '(C)',
 '(D)',
 '(A)',
 '(A)',
 '(A)',
 '(B)',
 '(D)',
 '(C)',
 '(B)',
 '(C)',
 '(A)',
 '(B)',
 '(D)',
 '(A)',
 '(D)',
 '(B)',
 '(B)',
 '(C)',
 '(B)',
 '(D)',
 '(B)',
 '(B)',
 '(C)',
 '(C)',
 '(D)',
 '(A)']